In [1]:
import ast
import csv
import json
import glom

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn2_circles

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

In [2]:
with open('../data/raw/fairsharing_dump_api_09_2021.json') as f:
    lines = f.read().splitlines()
    
fairsharing_df = pd.DataFrame(lines)
fairsharing_df.columns = ['json_element']
fairsharing_df['json_element'].apply(json.loads)
fairsharing_df = pd.json_normalize(fairsharing_df['json_element'].apply(json.loads))

fairsharing_df['unique_id'] = 'FAIRsharing_' + fairsharing_df.id
fairsharing_df = fairsharing_df.add_prefix('FAIRsharing_')
fairsharing_df.head()

FAIRsharing_id     FAIRsharing_type FAIRsharing_attributes.created-at  \
0           1723  fairsharing-records          2014-11-04T15:23:40.000Z   
1           3101  fairsharing-records          2020-09-16T08:49:13.000Z   
2           2649  fairsharing-records          2018-08-07T20:23:32.000Z   
3           2657  fairsharing-records          2018-08-13T15:12:11.000Z   
4           2078  fairsharing-records          2014-11-04T15:23:40.000Z   

  FAIRsharing_attributes.updated-at FAIRsharing_attributes.metadata.doi  \
0          2021-09-30T11:39:06.829Z         10.25504/FAIRsharing.8t18te   
1          2021-09-30T11:36:45.452Z                                 NaN   
2          2021-09-30T11:39:07.898Z                                 NaN   
3          2021-09-30T11:37:28.736Z         10.25504/FAIRsharing.tnByoG   
4          2021-09-30T11:34:43.129Z         10.25504/FAIRsharing.3axym7   

       FAIRsharing_attributes.metadata.name  \
0                        Cell Image Library   
1             WHOI Ship Data-Grabber System   
2  Electron Microscope Public Image Archive   
3              ClinicalStudyDataRequest.com   
4   Germplasm Resources Information Network   

  FAIRsharing_attributes.metadata.status  \
0                                  ready   
1                                  ready   
2                                  ready   
3                                  ready   
4                                  ready   

            FAIRsharing_attributes.metadata.contacts  \
0  [{'contact-name': 'David Orloff', 'contact-ema...   
1                                                NaN   
2  [{'contact-name': 'General contact', 'contact-...   
3  [{'contact-email': 'support@clinicalstudydatar...   
4           [{'contact-email': 'dbmu@ars-grin.gov'}]   

           FAIRsharing_attributes.metadata.homepage  \
0                   http://www.cellimagelibrary.org   
1  http://4dgeo.whoi.edu/shipdata/SDG_shipdata.html   
2           https://www.ebi.ac.uk/pdbe/emdb/empiar/   
3             https://clinicalstudydatarequest.com/   
4                         https://www.ars-grin.gov/   

   FAIRsharing_attributes.metadata.identifier  \
0                                        1723   
1                                        3101   
2                                        2649   
3                                        2657   
4                                        2078   

         FAIRsharing_attributes.metadata.description  \
0  This library is a public and easily accessible...   
1  The WHOI Ship DataGrabber system provides the ...   
2  EMPIAR, the Electron Microscopy Public Image A...   
3  ClinicalStudyDataRequest.com (CSDR) is a conso...   
4  GRIN provides National Genetic Resources Progr...   

       FAIRsharing_attributes.metadata.support-links  \
0  [{'url': 'http://www.cellimagelibrary.org/page...   
1  [{'url': 'http://4dgeo.whoi.edu/shipdata/SDG_o...   
2  [{'url': 'https://www.ebi.ac.uk/support/EMPIAR...   
3  [{'url': 'https://clinicalstudydatarequest.com...   
4  [{'url': 'https://www.ars-grin.gov/Pages/Colle...   

   FAIRsharing_attributes.metadata.year-creation  \
0                                         2010.0   
1                                         2004.0   
2                                         2015.0   
3                                         2014.0   
4                                         2010.0   

      FAIRsharing_attributes.metadata.data-processes  \
0  [{'name': 'live update', 'type': 'data release...   
1  [{'url': 'http://4dgeo.whoi.edu/sdg-bin/dv_mai...   
2  [{'url': 'https://www.ebi.ac.uk/pdbe/emdb/empi...   
3  [{'url': 'https://clinicalstudydatarequest.com...   
4  [{'url': 'https://www.ars-grin.gov/', 'name': ...   

  FAIRsharing_attributes.legacy-ids  \
0   [biodbcore-000180, bsg-d000180]   
1   [biodbcore-001609, bsg-d001609]   
2   [biodbcore-001140, bsg-d001140]   
3   [biodbcore-001149, bsg-d001149]   
4   [biodbcore-000546, bsg-d000546]   

  FAIRsharing_attributes.fairs

In [3]:
re3data_df = pd.read_csv('../data/raw/re3data.tsv', delimiter='\t',
                        converters={'subject': ast.literal_eval,
                                    'keyword': ast.literal_eval,
                                    'additionalName': ast.literal_eval,
                                    'repositoryIdentifier': ast.literal_eval,
                                    'type': ast.literal_eval,
                                    'contentType': ast.literal_eval,
                                    'providerType': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })

re3data_df['unique_id'] = 're3data_' + re3data_df.orgIdentifier
re3data_df = re3data_df.add_prefix('re3data_')
re3data_df.head()

re3data_OpenAIREID re3data_orgIdentifier  \
0  re3data_____::91780fe96da5ba32f804e43359c154ba          r3d100000001   
1  re3data_____::cc3ea05c863cd49af75f7f54e0e86f09          r3d100000002   
2  re3data_____::a2f73fbe91311f4356d0d7957c441773          r3d100000004   
3  re3data_____::0394b97eb11f19785cbca1ec830429da          r3d100000005   
4  re3data_____::a48f09c562b247a9919acfe195549b47          r3d100000006   

             re3data_repositoryName  \
0  Odum Institute Archive Dataverse   
1      Access to Archival Databases   
2    Datenbank Gesprochenes Deutsch   
3                     UNC Dataverse   
4          Archaeology Data Service   

                              re3data_additionalName  \
0                                                 []   
1                                              [AAD]   
2  [DGD, DGD2 (formerly), Database for Spoken Ger...   
3           [University of North Carolina Dataverse]   
4                                              [ADS]   

                      re3data_repositoryURL  \
0  https://dataverse.unc.edu/dataverse/odum   
1             https://aad.archives.gov/aad/   
2              https://dgd.ids-mannheim.de/   
3                https://dataverse.unc.edu/   
4     https://archaeologydataservice.ac.uk/   

                    re3data_repositoryIdentifier  \
0                                             []   
1             [RRID:SCR_010479, RRID:nlx_157752]   
2                                             []   
3                                             []   
4  [FAIRsharing_doi:10.25504/FAIRsharing.hm1mfg]   

                                 re3data_description     re3data_type  \
0  The Odum Institute Archive Dataverse contains ...   [disciplinary]   
1  You will find in the Access to Archival Databa...   [disciplinary]   
2  The "Database for Spoken German (DGD)" is a co...   [disciplinary]   
3  UNC Dataverse is an open-source repository sof...  [institutional]   
4  The ADS is an accredited digital repository fo...   [disciplinary]   

                                    re3data_size re3data_updateDate  \
0                  13 dataverses; 3.050 datasets         2020-12-04   
1                                            NaN                NaN   
2                                     34 corpora         2020-02-03   
3  186 dataverses; 25.272 studies; 229.442 files         2020-11-30   
4                                   1837 results         2020-05-20   

  re3data_startDate re3data_endDate  \
0               NaN             NaN   
1              1985             NaN   
2              2012             NaN   
3              2011             NaN   
4        1996-10-01             NaN   

                                     re3data_subject  \
0  [1 Humanities and Social Sciences, 111 Social ...   
1  [1 Humanities and Social Sciences, 102 History...   
2  [1 Humanities and Social Sciences, 104 Linguis...   
3  [1 Humanities and Social Sciences, 111 Social ...   
4  [1 Humanities and Social Sciences, 101 Ancient...   

   re3data_missionStatement  \
0                     False   
1                      True   
2                      True   
3                      True   
4                      True   

                                 re3data_contentType  \
0  [Databases, Plain text, Scientific and statist...   
1  [Images, Standard office documents, Structured...   
2  [Audiovisual data, Standard office documents, ...   
3  [Archived data, Plain text, Raw data, Scientif...   
4  [Archived data, Audiovisual data, Databases, I...   

              re3data_providerType  \
0                   [dataProvider]   
1                   [dataProvider]   
2  [dataProvider, serviceProvider]   
3  [dataProvider, serviceProvider]   
4  [dataProvider, serviceProvider]   

                                     re3data_keyword  \
0  [FAIR, Middle East, crime, demography, economy...   
1                                       [US History]   
2  [Australian German, FOLK, German dialects, Pfe... 

In [4]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'subject': ast.literal_eval,
                                    'alternativeNames': ast.literal_eval,
                                    'contentType': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    },
                         dtype={'orgIdentifier': str})

opendoar_df['unique_id'] = 'OpenDOAR_' + opendoar_df.orgIdentifier
opendoar_df = opendoar_df.add_prefix('OpenDOAR_')
opendoar_df.head()

OpenDOAR_OpenAIREID OpenDOAR_orgIdentifier  \
0  opendoar____::82161242827b703e6acf9c726942a1e4                    175   
1  opendoar____::ea5d2f1c4608232e07d3aa3d998e5135                     64   
2  opendoar____::a8f15eda80c50adb0e71943adc8015cf                    151   
3  opendoar____::65b9eea6e1cc6bb9f0cd2a47751a186f                    105   
4  opendoar____::38b3eff8baf56627478ec76a704e9b52                    101   

                             OpenDOAR_repositoryName  \
0                                  hku theses online   
1  research support scheme - central european uni...   
2                    cadmus, eui research repository   
3                           document server@uhasselt   
4                      utrecht university repository   

  OpenDOAR_alternativeNames               OpenDOAR_repositoryURL  \
0                        []  http://hub.hku.hk/handle/10722/1057   
1                        []          http://rss.archives.ceu.hu/   
2                        []                http://cadmus.eui.eu/   
3                        []   https://doclib.uhasselt.be/dspace/   
4                        []          http://dspace.library.uu.nl   

                                OpenDOAR_description  OpenDOAR_type  \
0  this is an institutional repository providing ...  institutional   
1  this is an institutional repository collecting...  institutional   
2  cadmus is the name of the eui research reposit...  institutional   
3  this site is a university repository providing...  institutional   
4  this site is a university repository providing...  institutional   

   OpenDOAR_updateDate   OpenDOAR_startDate  \
0  2021-03-25 10:16:18  2005-12-21 12:44:08   
1  2021-03-25 09:48:31  2006-01-04 14:59:30   
2  2021-09-13 13:35:36  2006-01-04 12:07:07   
3  2021-04-16 15:23:52  2006-01-24 15:46:44   
4  2021-04-16 15:22:03  2006-01-13 12:55:13   

                                    OpenDOAR_subject  \
0                                [multidisciplinary]   
1                                [multidisciplinary]   
2  [history and archaeology, multidisciplinary, s...   
3                                [multidisciplinary]   
4                                [multidisciplinary]   

                                OpenDOAR_contentType  \
0  [bibliographic_references, theses_and_disserta...   
1                 [unpub_reports_and_working_papers]   
2  [journal_articles, theses_and_dissertations, u...   
3  [journal_articles, conference_and_workshop_pap...   
4  [journal_articles, conference_and_workshop_pap...   

                                OpenDOAR_institution  OpenDOAR_metadataPolicy  \
0  [[university of hong kong, [香港大學, hku], cn, ht...                    False   
1  [[central european university, [ceu], hu, http...                    False   
2  [[european university institute, [eui], it, ht...                    False   
3  [[hasselt university, [universiteit hasselt, u...                    False   
4  [[university of utrecht, [universiteit utrecht...                    False   

   OpenDOAR_dataPolicy  OpenDOAR_submissionPolicy  OpenDOAR_contentPolicy  \
0                False                      False                   False   
1                False                      False                   False   
2                False                      False                   False   
3                False                      False                   False   
4                False                      False                   False   

            OpenDOAR_software OpenDOAR_api OpenDOAR_unique_id  
0  dspace cris-5.3.1-snapshot       false        OpenDOAR_175  
1               eprints 2.2.1        true         OpenDOAR_64  
2                  dspace 5.2        true        OpenDOAR_151  
3                dspace 1.7.2        true        OpenDOAR_105  
4                     dspace         true        OpenDOAR_101

In [5]:
roar_df = pd.read_csv('../data/raw/export_roar_CSV.csv', dtype='str')
roar_df = roar_df.groupby('eprintid').aggregate(set)

def value_or_list(cell_set):
    copy = set(cell_set)
    copy.discard(np.nan) 
    if len(copy) == 0:
        return np.nan
    if len(copy) == 1:
        return copy.pop()
    return list(copy)
        
roar_df = roar_df.applymap(value_or_list)
roar_df.reset_index(inplace=True)

roar_df['unique_id'] = 'roar_' + roar_df.eprintid
roar_df = roar_df.add_prefix('roar_')
roar_df.head()

roar_eprintid roar_rev_number roar_eprint_status roar_userid  roar_importid  \
0             1             633            archive           1            NaN   
1            10             511            archive           1            NaN   
2          1000             274            archive           1            NaN   
3         10001              20            archive          91            NaN   
4         10008              11            archive         404            NaN   

   roar_source           roar_dir       roar_datestamp         roar_lastmod  \
0          NaN  disk0/00/00/00/01  2010-01-06 13:43:48  2011-07-18 05:40:07   
1          NaN  disk0/00/00/00/10  2010-01-06 13:43:48  2011-07-18 05:40:13   
2          NaN  disk0/00/00/10/00  2010-01-06 13:45:01  2011-07-06 08:21:21   
3          NaN  disk0/00/01/00/01  2015-08-08 14:52:11  2016-03-21 19:44:01   
4          NaN  disk0/00/01/00/08  2015-08-08 14:52:26  2016-03-21 19:43:51   

   roar_status_changed      roar_type roar_succeeds  roar_commentary  \
0  2010-01-06 13:43:48        subject           NaN              NaN   
1  2010-01-06 13:43:48  institutional           NaN              NaN   
2  2010-01-06 13:45:01        subject           NaN              NaN   
3  2015-08-08 14:52:11        subject           NaN              NaN   
4  2015-08-08 14:52:26  institutional           NaN              NaN   

  roar_metadata_visibility  roar_latitude  roar_longitude  roar_relation_type  \
0                     show            NaN             NaN                 NaN   
1                     show            NaN             NaN                 NaN   
2                     show            NaN             NaN                 NaN   
3                     show            NaN             NaN                 NaN   
4                     show            NaN             NaN                 NaN   

   roar_relation_uri roar_item_issues_id roar_item_issues_type  \
0                NaN                 NaN                   NaN   
1                NaN                 NaN                   NaN   
2                NaN                 NaN                   NaN   
3                NaN                 NaN                   NaN   
4                NaN                 NaN                   NaN   

  roar_item_issues_description roar_item_issues_timestamp  \
0                          NaN                        NaN   
1                          NaN                        NaN   
2                          NaN                        NaN   
3                          NaN                        NaN   
4                          NaN                        NaN   

  roar_item_issues_status  roar_item_issues_reported_by  \
0                     NaN                           NaN   
1                     NaN                           NaN   
2                     NaN                           NaN   
3                     NaN                           NaN   
4                     NaN                           NaN   

   roar_item_issues_resolved_by  roar_item_issues_comment  \
0                           NaN                       NaN   
1                           NaN                       NaN   
2                           NaN                       NaN   
3                           NaN                       NaN   
4                           NaN                       NaN   

  roar_item_issues_count  roar_sword_depositor  roar_sword_slug roar_exemplar  \
0                      0                   NaN              NaN           NaN   
1                      0                   NaN              NaN           NaN   
2                      0                   NaN              NaN           NaN   
3                    NaN                   NaN              NaN           NaN   
4                    NaN                   NaN              NaN           NaN   

                                roar_home_page  \
0              http://archivesic.ccsd.cnrs.fr/   
1              http://www.diva-portal.org/mdh/ 

In [6]:
roar_df[roar_df.roar_eprintid == '10013']

roar_eprintid roar_rev_number roar_eprint_status roar_userid  roar_importid  \
7         10013              31            archive        7104            NaN   

   roar_source           roar_dir       roar_datestamp         roar_lastmod  \
7          NaN  disk0/00/01/00/13  2015-08-08 14:53:04  2016-03-21 19:54:43   

   roar_status_changed      roar_type roar_succeeds  roar_commentary  \
7  2015-08-08 14:53:04  institutional           NaN              NaN   

  roar_metadata_visibility  roar_latitude  roar_longitude  roar_relation_type  \
7                     show            NaN             NaN                 NaN   

   roar_relation_uri roar_item_issues_id roar_item_issues_type  \
7                NaN                 NaN                   NaN   

  roar_item_issues_description roar_item_issues_timestamp  \
7                          NaN                        NaN   

  roar_item_issues_status  roar_item_issues_reported_by  \
7                     NaN                           NaN   

   roar_item_issues_resolved_by  roar_item_issues_comment  \
7                           NaN                       NaN   

  roar_item_issues_count  roar_sword_depositor  roar_sword_slug roar_exemplar  \
7                    NaN                   NaN              NaN           NaN   

          roar_home_page                                         roar_title  \
7  http://er.ucu.edu.ua/  ErUCU: Electronic repository of the Ukrainian ...   

                       roar_oai_pmh          roar_sword_endpoint  \
7  http://er.ucu.edu.ua/oai/request  http://er.ucu.edu.ua/sword/   

                            roar_rss_feed roar_twitter_feed  \
7  http://er.ucu.edu.ua/feed/rss_2.0/site               NaN   

                                    roar_description roar_fulltext  \
7  Ukrainian Catholic University’s institutional ...          TRUE   

  roar_open_access roar_mandate        roar_organisation_title  \
7             TRUE         TRUE  Ukrainian Catholic University   

  roar_organisation_home_page roar_location_country roar_location_city  \
7      http://ucu.edu.ua/eng/                    ua               Lviv   

  roar_location_latitude roar_location_longitude roar_software  roar_geoname  \
7                    NaN                     NaN        dspace  geoname_2_UA   

  roar_version                                      roar_subjects  \
7        other  [B1, BS, BL, AC, D204, DK, HM, BF, L1, D1, H1,...   

             roar_date roar_note roar_suggestions roar_activity_low  \
7  2015-07-07 12:38:37       NaN              NaN               NaN   

  roar_activity_medium roar_activity_high roar_recordcount roar_recordhistory  \
7                  NaN                NaN              NaN                NaN   

  roar_fulltexts_total roar_fulltexts_docs roar_fulltexts_rtotal  \
7                  NaN                 NaN                   NaN   

  roar_fulltexts_rdocs     roar_registry_name roar_registry_id roar_submit_to  \
7                  NaN  [opendoar, celestial]     [5883, 3410]            NaN   

  roar_submitted_to_name roar_submitted_to_done roar_webometrics_rank  \
7                    NaN                    NaN                   NaN   

  roar_webometrics_size roar_webometrics_visibility  \
7                   NaN                         NaN   

  roar_webometrics_rich_files roar_webometrics_scholar roar_monthly_deposits  \
7                         NaN                      NaN                   NaN   

  roar_total_deposits             roar_association roar_unique_id  
7                 NaN  [russell_group, ivy_league]     roar_10013

# Loading dedup results

In [7]:
dup = pd.read_csv('../data/interim/fairsharing_dedup.csv', sep=';', quotechar='"', header=None, names=['dedup_id', 'duplicate_id', 'original_id', 'name', 'source'])
dup['unique_id'] = dup.source + '_' + dup.original_id
dup.head()

dedup_id  \
0  dedup::860320be12a1c050cd7731794e231bd3   
1  dedup::1aa7a8773e6a7fdacbcedf9999009a38   
2  dedup::31bceb0c3e2a260593e1e36655ebcee4   
3  dedup::e37b08dd3015330dcbb5d6663667b8b8   
4  dedup::2841194266115ac1cc04d19630cde46b   

                                     duplicate_id   original_id  \
0  opendoar____::2290a7385ed77cc5592dc2153229f082          1064   
1  opendoar____::191f8f858acda435ae0daf994e2a72c2          8648   
2  opendoar____::d5776aeecb3c45ab15adce6f5cb355f3          9713   
3  opendoar____::18997733ec258a9fcaf239cc55d53363           427   
4  re3data_____::3afbb2b45a3dd218a5a091ca773cf6c5  r3d100011189   

                                                name    source  \
0                 oxford university research archive  OpenDOAR   
1                   digital commons@georgia southern  OpenDOAR   
2                          materials data repository  OpenDOAR   
3   digital repository at the university of maryland  OpenDOAR   
4  PRISM: University of Calgary's Digital Repository   re3data   

              unique_id  
0         OpenDOAR_1064  
1         OpenDOAR_8648  
2         OpenDOAR_9713  
3          OpenDOAR_427  
4  re3data_r3d100011189

In [8]:
dup.describe()

dedup_id  \
count                                      4617   
unique                                     2191   
top     dedup::75e33da9b103b7b91dcd8da0abe1354b   
freq                                          5   

                                          duplicate_id original_id  \
count                                             4617        4617   
unique                                            4617        4159   
top     opendoar____::2290a7385ed77cc5592dc2153229f082        2399   
freq                                                 1           3   

                        name source      unique_id  
count                   4617   4617           4617  
unique                  3968      4           4617  
top     UPN JATIM REPOSITORY   roar  OpenDOAR_1064  
freq                       4   1977              1

In [9]:
dup_grouped = dup.groupby('dedup_id').aggregate(list)
dup_grouped['source_set'] = dup_grouped.source.map(set)

In [10]:
dup_grouped[dup_grouped.source_set.str.len() == 4].count()

duplicate_id    6
original_id     6
name            6
source          6
unique_id       6
source_set      6
dtype: int64

In [11]:
dup_grouped[dup_grouped.source_set.str.len() == 3].count()

duplicate_id    60
original_id     60
name            60
source          60
unique_id       60
source_set      60
dtype: int64

In [12]:
dup_grouped[dup_grouped.source_set.str.len() == 2].count()

duplicate_id    1986
original_id     1986
name            1986
source          1986
unique_id       1986
source_set      1986
dtype: int64

In [13]:
dup_grouped[dup_grouped.source_set.str.len() == 1].count()

duplicate_id    139
original_id     139
name            139
source          139
unique_id       139
source_set      139
dtype: int64

# Isolating duplicates within a registry

In [14]:
dup_within = dup.groupby('dedup_id').aggregate(list)
dup_within['source_set'] = dup_within.source.map(set)
dup_within = dup_within[dup_within.source_set.str.len() == 1]
dup_within.head()

duplicate_id  \
dedup_id                                                      
dedup::000871c1fc726f0b52dc86a4eeb027de        [4612, 4649]   
dedup::0163cceb20f5ca7b313419c068abd9dc        [7943, 8003]   
dedup::028ee724157b05d04e7bdcf237d12e60  [2670, 2698, 2741]   
dedup::03593ce517feac573fdaafa6dcedef61        [4393, 4394]   
dedup::03e0704b5690a2dee1861dc3ad3316c9        [1019, 5550]   

                                                original_id  \
dedup_id                                                      
dedup::000871c1fc726f0b52dc86a4eeb027de        [4612, 4649]   
dedup::0163cceb20f5ca7b313419c068abd9dc        [7943, 8003]   
dedup::028ee724157b05d04e7bdcf237d12e60  [2670, 2698, 2741]   
dedup::03593ce517feac573fdaafa6dcedef61        [4393, 4394]   
dedup::03e0704b5690a2dee1861dc3ad3316c9        [1019, 5550]   

                                                                                      name  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de  [IIT Bombay Institutional Repository, IIT Bomb...   
dedup::0163cceb20f5ca7b313419c068abd9dc  [EPrints@NIRT Library Welcomes! - EPrints@NITR...   
dedup::028ee724157b05d04e7bdcf237d12e60  [HSF Brage Open Research Archive, HSF Brage Op...   
dedup::03593ce517feac573fdaafa6dcedef61  [Institutional Repository of Kunming Institute...   
dedup::03e0704b5690a2dee1861dc3ad3316c9  [PolyU Institutional Repository, PolyU Institu...   

                                                     source  \
dedup_id                                                      
dedup::000871c1fc726f0b52dc86a4eeb027de        [roar, roar]   
dedup::0163cceb20f5ca7b313419c068abd9dc        [roar, roar]   
dedup::028ee724157b05d04e7bdcf237d12e60  [roar, roar, roar]   
dedup::03593ce517feac573fdaafa6dcedef61        [roar, roar]   
dedup::03e0704b5690a2dee1861dc3ad3316c9        [roar, roar]   

                                                                 unique_id  \
dedup_id                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de             [roar_4612, roar_4649]   
dedup::0163cceb20f5ca7b313419c068abd9dc             [roar_7943, roar_8003]   
dedup::028ee724157b05d04e7bdcf237d12e60  [roar_2670, roar_2698, roar_2741]   
dedup::03593ce517feac573fdaafa6dcedef61             [roar_4393, roar_4394]   
dedup::03e0704b5690a2dee1861dc3ad3316c9             [roar_1019, roar_5550]   

                                        source_set  
dedup_id                                            
dedup::000871c1fc726f0b52dc86a4eeb027de     {roar}  
dedup::0163cceb20f5ca7b313419c068abd9dc     {roar}  
dedup::028ee724157b05d04e7bdcf237d12e60     {roar}  
dedup::03593ce517feac573fdaafa6dcedef61     {roar}  
dedup::03e0704b5690a2dee1861dc3ad3316c9     {roar}

In [15]:
dup_within['source_set'] = dup_within.source_set.map(set.pop)
dup_within.head()

duplicate_id  \
dedup_id                                                      
dedup::000871c1fc726f0b52dc86a4eeb027de        [4612, 4649]   
dedup::0163cceb20f5ca7b313419c068abd9dc        [7943, 8003]   
dedup::028ee724157b05d04e7bdcf237d12e60  [2670, 2698, 2741]   
dedup::03593ce517feac573fdaafa6dcedef61        [4393, 4394]   
dedup::03e0704b5690a2dee1861dc3ad3316c9        [1019, 5550]   

                                                original_id  \
dedup_id                                                      
dedup::000871c1fc726f0b52dc86a4eeb027de        [4612, 4649]   
dedup::0163cceb20f5ca7b313419c068abd9dc        [7943, 8003]   
dedup::028ee724157b05d04e7bdcf237d12e60  [2670, 2698, 2741]   
dedup::03593ce517feac573fdaafa6dcedef61        [4393, 4394]   
dedup::03e0704b5690a2dee1861dc3ad3316c9        [1019, 5550]   

                                                                                      name  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de  [IIT Bombay Institutional Repository, IIT Bomb...   
dedup::0163cceb20f5ca7b313419c068abd9dc  [EPrints@NIRT Library Welcomes! - EPrints@NITR...   
dedup::028ee724157b05d04e7bdcf237d12e60  [HSF Brage Open Research Archive, HSF Brage Op...   
dedup::03593ce517feac573fdaafa6dcedef61  [Institutional Repository of Kunming Institute...   
dedup::03e0704b5690a2dee1861dc3ad3316c9  [PolyU Institutional Repository, PolyU Institu...   

                                                     source  \
dedup_id                                                      
dedup::000871c1fc726f0b52dc86a4eeb027de        [roar, roar]   
dedup::0163cceb20f5ca7b313419c068abd9dc        [roar, roar]   
dedup::028ee724157b05d04e7bdcf237d12e60  [roar, roar, roar]   
dedup::03593ce517feac573fdaafa6dcedef61        [roar, roar]   
dedup::03e0704b5690a2dee1861dc3ad3316c9        [roar, roar]   

                                                                 unique_id  \
dedup_id                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de             [roar_4612, roar_4649]   
dedup::0163cceb20f5ca7b313419c068abd9dc             [roar_7943, roar_8003]   
dedup::028ee724157b05d04e7bdcf237d12e60  [roar_2670, roar_2698, roar_2741]   
dedup::03593ce517feac573fdaafa6dcedef61             [roar_4393, roar_4394]   
dedup::03e0704b5690a2dee1861dc3ad3316c9             [roar_1019, roar_5550]   

                                        source_set  
dedup_id                                            
dedup::000871c1fc726f0b52dc86a4eeb027de       roar  
dedup::0163cceb20f5ca7b313419c068abd9dc       roar  
dedup::028ee724157b05d04e7bdcf237d12e60       roar  
dedup::03593ce517feac573fdaafa6dcedef61       roar  
dedup::03e0704b5690a2dee1861dc3ad3316c9       roar

In [16]:
dup_within.groupby('source_set').count()

duplicate_id  original_id  name  source  unique_id
source_set                                                    
OpenDOAR              16           16    16      16         16
re3data                2            2     2       2          2
roar                 121          121   121     121        121

In [17]:
dup_within = dup[dup.dedup_id.isin(dup_within.index)]
dup_within

dedup_id duplicate_id original_id  \
28    dedup::d2ddea18f00665ce8623e36bd4e3c7c5         8237        8237   
31    dedup::4c5bcfec8584af0d967f1ab10179ca4b         2820        2820   
46    dedup::c2ae5cb2426d96ed19a50b0b7d7c8e11         9487        9487   
53    dedup::1c65cef3dfd1e00c0b03923a1c591db4         1241        1241   
59    dedup::4217ec5d78c4bc4e5bd006783482441f        15142       15142   
...                                       ...          ...         ...   
4560  dedup::fc394e9935fbd62c8aedc372464e1965         7161        7161   
4586  dedup::000871c1fc726f0b52dc86a4eeb027de         4649        4649   
4587  dedup::72c288a828485e5b1d4c52910d106734        16867       16867   
4598  dedup::0163cceb20f5ca7b313419c068abd9dc         8003        8003   
4608  dedup::2aeb1a8f8475cef63900be5d0780e872        15471       15471   

                                                   name source   unique_id  
28           AIR | Archivio Istituzionale della Ricerca   roar   roar_8237  
31               USU Repository: Open Access Repository   roar   roar_2820  
46                                      IR at NRF: Home   roar   roar_9487  
53           Swansea Metropolitan University Repository   roar   roar_1241  
59                            Repositorio Institucional   roar  roar_15142  
...                                                 ...    ...         ...  
4560                                 Welcome to IR@NPL    roar   roar_7161  
4586                IIT Bombay Institutional Repository   roar   roar_4649  
4587  Chung Shan Medical University Institutional Re...   roar  roar_16867  
4598      EPrints@NIRT Library Welcomes! - EPrints@NIRT   roar   roar_8003  
4608                    Repository STIE Nobel Indonesia   roar  roar_15471  

[287 rows x 6 columns]

# Isolating duplicates across registries (hybrid)

In [18]:
dup_across = dup[~dup.dedup_id.isin(dup_within.dedup_id)]
dup_across = dup_across.groupby('dedup_id').aggregate(list)
dup_across['source_set'] = dup_across.source.map(set)

dup_hybrid = dup_across[dup_across.source_set.str.len() < dup_across.source.str.len()]
dup_hybrid = dup[dup.dedup_id.isin(dup_hybrid.index)]
dup_hybrid

dedup_id  \
12    dedup::471c50ad1a156d7256eddfd747d77931   
21    dedup::69dafe8b58066478aea48f3d0f384820   
26    dedup::8f822ac814829da24a7065b8131bdf47   
41    dedup::63a99723ebb3af94d52b474c3b21dbe1   
47    dedup::82680bfec0fa08346c1b10d30a3e3d4a   
...                                       ...   
4601  dedup::7810ccd41bf26faaa2c4e1f20db70a71   
4602  dedup::e655c7716a4b3ea67f48c6322fc42ed6   
4603  dedup::5ebe5626b9f1cd89fbb9f665a527591f   
4605  dedup::ec0bfd000f253eff3acb1043e1c06979   
4610  dedup::1c7836dbabd12c458d20e3b35633733a   

                                        duplicate_id original_id  \
12    opendoar____::6351bf9dce654515bf1ddbd6426dfa97        1996   
21                                              2312        2312   
26    opendoar____::a34bacf839b923770b2c360eefa26748        1035   
41                                              5779        5779   
47                                             11212       11212   
...                                              ...         ...   
4601                                            3172        3172   
4602  opendoar____::52c5189391854c93e8a0e1326e56c14f        1637   
4603                                           16225       16225   
4605  opendoar____::aa2a77371374094fe9e0bc1de3f94ed9        1829   
4610                                           14616       14616   

                                                   name    source  \
12                       ehtc repositorio institucional  OpenDOAR   
21    Göteborgs universitets publikationer - e-publi...      roar   
26            kitami institute of technology repository  OpenDOAR   
41                                Sanok Digital Library      roar   
47        Publication Server of the Wuppertal Institute      roar   
...                                                 ...       ...   
4601                            Tesis Electrónicas UACh      roar   
4602                           vtext digital repository  OpenDOAR   
4603  Necmettin Erbakan University Institutional Rep...      roar   
4605                                            npue ir  OpenDOAR   
4610   SOAR@USA: Scholarship and Open Access Repository      roar   

          unique_id  
12    OpenDOAR_1996  
21        roar_2312  
26    OpenDOAR_1035  
41        roar_5779  
47       roar_11212  
...             ...  
4601      roar_3172  
4602  OpenDOAR_1637  
4603     roar_16225  
4605  OpenDOAR_1829  
4610     roar_14616  

[440 rows x 6 columns]

# Isolating duplicates across registries (pure)

In [19]:
dup_across = dup_across[dup_across.source_set.str.len() == dup_across.source.str.len()]
dup_across = dup[dup.dedup_id.isin(dup_across.index)]
dup_across
# dup[dup.dedup_id.isin(dup_across.index)]

dedup_id  \
0     dedup::860320be12a1c050cd7731794e231bd3   
1     dedup::1aa7a8773e6a7fdacbcedf9999009a38   
2     dedup::31bceb0c3e2a260593e1e36655ebcee4   
3     dedup::e37b08dd3015330dcbb5d6663667b8b8   
4     dedup::2841194266115ac1cc04d19630cde46b   
...                                       ...   
4612  dedup::5ef0b4eba35ab2d6180b0bca7e46b6f9   
4613  dedup::66e8d052ec2230c66bd11ee6b5a0e3c8   
4614  dedup::1216a1bca4361c39d1d77965c5d95ee3   
4615  dedup::1408358fe6a7f9327dd41a5651ac284c   
4616  dedup::5cc33dfe7e069a757ca0fcbe6b95c89e   

                                        duplicate_id   original_id  \
0     opendoar____::2290a7385ed77cc5592dc2153229f082          1064   
1     opendoar____::191f8f858acda435ae0daf994e2a72c2          8648   
2     opendoar____::d5776aeecb3c45ab15adce6f5cb355f3          9713   
3     opendoar____::18997733ec258a9fcaf239cc55d53363           427   
4     re3data_____::3afbb2b45a3dd218a5a091ca773cf6c5  r3d100011189   
...                                              ...           ...   
4612                                             475           475   
4613                                           14199         14199   
4614                                            4960          4960   
4615                                           13824         13824   
4616  opendoar____::d8a4e572d866aa45da78418d9d2ff9f9          4351   

                                                   name    source  \
0                    oxford university research archive  OpenDOAR   
1                      digital commons@georgia southern  OpenDOAR   
2                             materials data repository  OpenDOAR   
3      digital repository at the university of maryland  OpenDOAR   
4     PRISM: University of Calgary's Digital Repository   re3data   
...                                                 ...       ...   
4612  Ecological Restoration Institute - Northern Ar...      roar   
4613                      Repositori STKIP PGRI Sumenep      roar   
4614                Virtual Archive of Polish Armenians      roar   
4615  Digital Commons @ New Jersey Institute of Tech...      roar   
4616                                odu digital commons  OpenDOAR   

                 unique_id  
0            OpenDOAR_1064  
1            OpenDOAR_8648  
2            OpenDOAR_9713  
3             OpenDOAR_427  
4     re3data_r3d100011189  
...                    ...  
4612              roar_475  
4613            roar_14199  
4614             roar_4960  
4615            roar_13824  
4616         OpenDOAR_4351  

[3890 rows x 6 columns]

Double check partitions

In [20]:
dup.count()

dedup_id        4617
duplicate_id    4617
original_id     4617
name            4617
source          4617
unique_id       4617
dtype: int64

In [21]:
dup_across.count() + dup_within.count() + dup_hybrid.count()

dedup_id        4617
duplicate_id    4617
original_id     4617
name            4617
source          4617
unique_id       4617
dtype: int64

In [22]:
dup_within.groupby('dedup_id').ngroups + dup_across.groupby('dedup_id').ngroups + dup_hybrid.groupby('dedup_id').ngroups

2191

In [23]:
dup.groupby('dedup_id').ngroups

2191

# Joining information

In [24]:
dup_within = dup_within.merge(fairsharing_df, left_on='unique_id', right_on='FAIRsharing_unique_id', how='left')
dup_within = dup_within.merge(re3data_df, left_on='unique_id', right_on='re3data_unique_id', how='left')
dup_within = dup_within.merge(opendoar_df, left_on='unique_id', right_on='OpenDOAR_unique_id', how='left')
dup_within = dup_within.merge(roar_df, left_on='unique_id', right_on='roar_unique_id', how='left')
dup_within.head()

dedup_id duplicate_id original_id  \
0  dedup::d2ddea18f00665ce8623e36bd4e3c7c5         8237        8237   
1  dedup::4c5bcfec8584af0d967f1ab10179ca4b         2820        2820   
2  dedup::c2ae5cb2426d96ed19a50b0b7d7c8e11         9487        9487   
3  dedup::1c65cef3dfd1e00c0b03923a1c591db4         1241        1241   
4  dedup::4217ec5d78c4bc4e5bd006783482441f        15142       15142   

                                         name source   unique_id  \
0  AIR | Archivio Istituzionale della Ricerca   roar   roar_8237   
1      USU Repository: Open Access Repository   roar   roar_2820   
2                             IR at NRF: Home   roar   roar_9487   
3  Swansea Metropolitan University Repository   roar   roar_1241   
4                   Repositorio Institucional   roar  roar_15142   

  FAIRsharing_id FAIRsharing_type FAIRsharing_attributes.created-at  \
0            NaN              NaN                               NaN   
1            NaN              NaN                               NaN   
2            NaN              NaN                               NaN   
3            NaN              NaN                               NaN   
4            NaN              NaN                               NaN   

  FAIRsharing_attributes.updated-at FAIRsharing_attributes.metadata.doi  \
0                               NaN                                 NaN   
1                               NaN                                 NaN   
2                               NaN                                 NaN   
3                               NaN                                 NaN   
4                               NaN                                 NaN   

  FAIRsharing_attributes.metadata.name FAIRsharing_attributes.metadata.status  \
0                                  NaN                                    NaN   
1                                  NaN                                    NaN   
2                                  NaN                                    NaN   
3                                  NaN                                    NaN   
4                                  NaN                                    NaN   

  FAIRsharing_attributes.metadata.contacts  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

  FAIRsharing_attributes.metadata.homepage  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

   FAIRsharing_attributes.metadata.identifier  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.description  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.support-links  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   

   FAIRsharing_attributes.metadata.year-creation  \
0                                            NaN   
1                                            NaN   
2                                            NaN   
3                                            NaN   
4                                            NaN   

  FAIRsharing_attributes.metadata.data-processes  \
0                

In [25]:
dup_hybrid = dup_hybrid.merge(fairsharing_df, left_on='unique_id', right_on='FAIRsharing_unique_id', how='left')
dup_hybrid = dup_hybrid.merge(re3data_df, left_on='unique_id', right_on='re3data_unique_id', how='left')
dup_hybrid = dup_hybrid.merge(opendoar_df, left_on='unique_id', right_on='OpenDOAR_unique_id', how='left')
dup_hybrid = dup_hybrid.merge(roar_df, left_on='unique_id', right_on='roar_unique_id', how='left')
dup_hybrid.head()

dedup_id  \
0  dedup::471c50ad1a156d7256eddfd747d77931   
1  dedup::69dafe8b58066478aea48f3d0f384820   
2  dedup::8f822ac814829da24a7065b8131bdf47   
3  dedup::63a99723ebb3af94d52b474c3b21dbe1   
4  dedup::82680bfec0fa08346c1b10d30a3e3d4a   

                                     duplicate_id original_id  \
0  opendoar____::6351bf9dce654515bf1ddbd6426dfa97        1996   
1                                            2312        2312   
2  opendoar____::a34bacf839b923770b2c360eefa26748        1035   
3                                            5779        5779   
4                                           11212       11212   

                                                name    source      unique_id  \
0                     ehtc repositorio institucional  OpenDOAR  OpenDOAR_1996   
1  Göteborgs universitets publikationer - e-publi...      roar      roar_2312   
2          kitami institute of technology repository  OpenDOAR  OpenDOAR_1035   
3                              Sanok Digital Library      roar      roar_5779   
4      Publication Server of the Wuppertal Institute      roar     roar_11212   

  FAIRsharing_id FAIRsharing_type FAIRsharing_attributes.created-at  \
0            NaN              NaN                               NaN   
1            NaN              NaN                               NaN   
2            NaN              NaN                               NaN   
3            NaN              NaN                               NaN   
4            NaN              NaN                               NaN   

  FAIRsharing_attributes.updated-at FAIRsharing_attributes.metadata.doi  \
0                               NaN                                 NaN   
1                               NaN                                 NaN   
2                               NaN                                 NaN   
3                               NaN                                 NaN   
4                               NaN                                 NaN   

  FAIRsharing_attributes.metadata.name FAIRsharing_attributes.metadata.status  \
0                                  NaN                                    NaN   
1                                  NaN                                    NaN   
2                                  NaN                                    NaN   
3                                  NaN                                    NaN   
4                                  NaN                                    NaN   

  FAIRsharing_attributes.metadata.contacts  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

  FAIRsharing_attributes.metadata.homepage  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

   FAIRsharing_attributes.metadata.identifier  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.description  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.support-links  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   

   FAIRsharing_attributes.metadata.year-creation  \
0          

In [26]:
dup_across = dup_across.merge(fairsharing_df, left_on='unique_id', right_on='FAIRsharing_unique_id', how='left')
dup_across = dup_across.merge(re3data_df, left_on='unique_id', right_on='re3data_unique_id', how='left')
dup_across = dup_across.merge(opendoar_df, left_on='unique_id', right_on='OpenDOAR_unique_id', how='left')
dup_across = dup_across.merge(roar_df, left_on='unique_id', right_on='roar_unique_id', how='left')
dup_across.head()

dedup_id  \
0  dedup::860320be12a1c050cd7731794e231bd3   
1  dedup::1aa7a8773e6a7fdacbcedf9999009a38   
2  dedup::31bceb0c3e2a260593e1e36655ebcee4   
3  dedup::e37b08dd3015330dcbb5d6663667b8b8   
4  dedup::2841194266115ac1cc04d19630cde46b   

                                     duplicate_id   original_id  \
0  opendoar____::2290a7385ed77cc5592dc2153229f082          1064   
1  opendoar____::191f8f858acda435ae0daf994e2a72c2          8648   
2  opendoar____::d5776aeecb3c45ab15adce6f5cb355f3          9713   
3  opendoar____::18997733ec258a9fcaf239cc55d53363           427   
4  re3data_____::3afbb2b45a3dd218a5a091ca773cf6c5  r3d100011189   

                                                name    source  \
0                 oxford university research archive  OpenDOAR   
1                   digital commons@georgia southern  OpenDOAR   
2                          materials data repository  OpenDOAR   
3   digital repository at the university of maryland  OpenDOAR   
4  PRISM: University of Calgary's Digital Repository   re3data   

              unique_id FAIRsharing_id FAIRsharing_type  \
0         OpenDOAR_1064            NaN              NaN   
1         OpenDOAR_8648            NaN              NaN   
2         OpenDOAR_9713            NaN              NaN   
3          OpenDOAR_427            NaN              NaN   
4  re3data_r3d100011189            NaN              NaN   

  FAIRsharing_attributes.created-at FAIRsharing_attributes.updated-at  \
0                               NaN                               NaN   
1                               NaN                               NaN   
2                               NaN                               NaN   
3                               NaN                               NaN   
4                               NaN                               NaN   

  FAIRsharing_attributes.metadata.doi FAIRsharing_attributes.metadata.name  \
0                                 NaN                                  NaN   
1                                 NaN                                  NaN   
2                                 NaN                                  NaN   
3                                 NaN                                  NaN   
4                                 NaN                                  NaN   

  FAIRsharing_attributes.metadata.status  \
0                                    NaN   
1                                    NaN   
2                                    NaN   
3                                    NaN   
4                                    NaN   

  FAIRsharing_attributes.metadata.contacts  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

  FAIRsharing_attributes.metadata.homepage  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

   FAIRsharing_attributes.metadata.identifier  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.description  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.support-links  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                             

In [27]:
dup_within = dup_within.groupby('dedup_id').aggregate(list).reset_index()
dup_within['source_set'] = dup_within.source.map(set)
dup_within.head()

<ipython-input-27-3881fa0a0224>:1: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

<ipython-input-27-3881fa0a0224>:2: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`



dedup_id        duplicate_id  \
0  dedup::000871c1fc726f0b52dc86a4eeb027de        [4612, 4649]   
1  dedup::0163cceb20f5ca7b313419c068abd9dc        [7943, 8003]   
2  dedup::028ee724157b05d04e7bdcf237d12e60  [2670, 2698, 2741]   
3  dedup::03593ce517feac573fdaafa6dcedef61        [4393, 4394]   
4  dedup::03e0704b5690a2dee1861dc3ad3316c9        [1019, 5550]   

          original_id                                               name  \
0        [4612, 4649]  [IIT Bombay Institutional Repository, IIT Bomb...   
1        [7943, 8003]  [EPrints@NIRT Library Welcomes! - EPrints@NITR...   
2  [2670, 2698, 2741]  [HSF Brage Open Research Archive, HSF Brage Op...   
3        [4393, 4394]  [Institutional Repository of Kunming Institute...   
4        [1019, 5550]  [PolyU Institutional Repository, PolyU Institu...   

               source                          unique_id   FAIRsharing_id  \
0        [roar, roar]             [roar_4612, roar_4649]       [nan, nan]   
1        [roar, roar]             [roar_7943, roar_8003]       [nan, nan]   
2  [roar, roar, roar]  [roar_2670, roar_2698, roar_2741]  [nan, nan, nan]   
3        [roar, roar]             [roar_4393, roar_4394]       [nan, nan]   
4        [roar, roar]             [roar_1019, roar_5550]       [nan, nan]   

  FAIRsharing_type FAIRsharing_attributes.created-at  \
0       [nan, nan]                        [nan, nan]   
1       [nan, nan]                        [nan, nan]   
2  [nan, nan, nan]                   [nan, nan, nan]   
3       [nan, nan]                        [nan, nan]   
4       [nan, nan]                        [nan, nan]   

  FAIRsharing_attributes.updated-at FAIRsharing_attributes.metadata.doi  \
0                        [nan, nan]                          [nan, nan]   
1                        [nan, nan]                          [nan, nan]   
2                   [nan, nan, nan]                     [nan, nan, nan]   
3                        [nan, nan]                          [nan, nan]   
4                        [nan, nan]                          [nan, nan]   

  FAIRsharing_attributes.metadata.name FAIRsharing_attributes.metadata.status  \
0                           [nan, nan]                             [nan, nan]   
1                           [nan, nan]                             [nan, nan]   
2                      [nan, nan, nan]                        [nan, nan, nan]   
3                           [nan, nan]                             [nan, nan]   
4                           [nan, nan]                             [nan, nan]   

  FAIRsharing_attributes.metadata.contacts  \
0                               [nan, nan]   
1                               [nan, nan]   
2                          [nan, nan, nan]   
3                               [nan, nan]   
4                               [nan, nan]   

  FAIRsharing_attributes.metadata.homepage  \
0                               [nan, nan]   
1                               [nan, nan]   
2                          [nan, nan, nan]   
3                               [nan, nan]   
4                               [nan, nan]   

  FAIRsharing_attributes.metadata.identifier  \
0                                 [nan, nan]   
1                                 [nan, nan]   
2                            [nan, nan, nan]   
3                                 [nan, nan]   
4                                 [nan, nan]   

  FAIRsharing_attributes.metadata.description  \
0                                  [nan, nan]   
1                                  [nan, nan]   
2                             [nan, nan, nan]   
3                                  [nan, nan]   
4                                  [nan, nan]   

  FAIRsharing_attributes.metadata.support-links  \
0                                    [nan, nan]   
1                                    [nan, nan]   
2                               [nan, nan, nan]   
3                                    [nan, nan]   
4                                    [nan, nan]  

In [28]:
dup_hybrid = dup_hybrid.groupby('dedup_id').aggregate(list).reset_index()
dup_hybrid['source_set'] = dup_hybrid.source.map(set)
dup_hybrid.head()

<ipython-input-28-89649d18870f>:1: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

<ipython-input-28-89649d18870f>:2: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`



dedup_id  \
0  dedup::01b6397888c09d84f3dc89d807aa1004   
1  dedup::03db60c2331018b18c4166c1787072fe   
2  dedup::05128e44e27c36bdba71221bfccf735d   
3  dedup::069059b7ef840f0c74a814ec9237b6ec   
4  dedup::0e139b17a92b2df7d6c3c840e51465fe   

                                        duplicate_id         original_id  \
0  [4745, opendoar____::a9365bd906e11324065c35be4...  [4745, 2429, 4320]   
1  [opendoar____::78bc62d08a9a0b9b0b9c0ad339ef82d...  [3087, 4500, 8504]   
2  [opendoar____::426f990b332ef8193a61cc90516c124...  [2318, 5503, 4271]   
3  [5711, 126, opendoar____::1cd3882394520876dc88...   [5711, 126, 1509]   
4  [4379, 4266, opendoar____::f976b57bb9dd27aa2e7...  [4379, 4266, 2306]   

                                                name  \
0      [RU-Económicas, ru-económicas, ru económicas]   
1  [landmark university repository, landmark univ...   
2  [iława biblioteka cyrfrowa (iława digital libr...   
3  [Bibioteca Digital Ação Educativa, Biblioteca ...   
4  [Institutional Repository of Ningbo Institute ...   

                       source                                  unique_id  \
0  [roar, OpenDOAR, OpenDOAR]  [roar_4745, OpenDOAR_2429, OpenDOAR_4320]   
1  [OpenDOAR, OpenDOAR, roar]  [OpenDOAR_3087, OpenDOAR_4500, roar_8504]   
2      [OpenDOAR, roar, roar]      [OpenDOAR_2318, roar_5503, roar_4271]   
3      [roar, roar, OpenDOAR]       [roar_5711, roar_126, OpenDOAR_1509]   
4      [roar, roar, OpenDOAR]      [roar_4379, roar_4266, OpenDOAR_2306]   

    FAIRsharing_id FAIRsharing_type FAIRsharing_attributes.created-at  \
0  [nan, nan, nan]  [nan, nan, nan]                   [nan, nan, nan]   
1  [nan, nan, nan]  [nan, nan, nan]                   [nan, nan, nan]   
2  [nan, nan, nan]  [nan, nan, nan]                   [nan, nan, nan]   
3  [nan, nan, nan]  [nan, nan, nan]                   [nan, nan, nan]   
4  [nan, nan, nan]  [nan, nan, nan]                   [nan, nan, nan]   

  FAIRsharing_attributes.updated-at FAIRsharing_attributes.metadata.doi  \
0                   [nan, nan, nan]                     [nan, nan, nan]   
1                   [nan, nan, nan]                     [nan, nan, nan]   
2                   [nan, nan, nan]                     [nan, nan, nan]   
3                   [nan, nan, nan]                     [nan, nan, nan]   
4                   [nan, nan, nan]                     [nan, nan, nan]   

  FAIRsharing_attributes.metadata.name FAIRsharing_attributes.metadata.status  \
0                      [nan, nan, nan]                        [nan, nan, nan]   
1                      [nan, nan, nan]                        [nan, nan, nan]   
2                      [nan, nan, nan]                        [nan, nan, nan]   
3                      [nan, nan, nan]                        [nan, nan, nan]   
4                      [nan, nan, nan]                        [nan, nan, nan]   

  FAIRsharing_attributes.metadata.contacts  \
0                          [nan, nan, nan]   
1                          [nan, nan, nan]   
2                          [nan, nan, nan]   
3                          [nan, nan, nan]   
4                          [nan, nan, nan]   

  FAIRsharing_attributes.metadata.homepage  \
0                          [nan, nan, nan]   
1                          [nan, nan, nan]   
2                          [nan, nan, nan]   
3                          [nan, nan, nan]   
4                          [nan, nan, nan]   

  FAIRsharing_attributes.metadata.identifier  \
0                            [nan, nan, nan]   
1                            [nan, nan, nan]   
2                            [nan, nan, nan]   
3                            [nan, nan, nan]   
4                            [nan, nan, nan]   

  FAIRsharing_attributes.metadata.description  \
0                             [nan, nan, nan]   
1                             [nan, nan, nan]   
2                             [nan, nan, nan]   
3                             [nan, nan, nan]   
4                             [nan, nan, 

In [29]:
dup_across = dup_across.groupby('dedup_id').aggregate(list).reset_index()
dup_across['source_set'] = dup_across.source.map(set)
dup_across.head()

<ipython-input-29-7abf9225ca42>:1: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

<ipython-input-29-7abf9225ca42>:2: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`



dedup_id  \
0  dedup::001e6d882e54c780ce269d3c46997287   
1  dedup::0023a1e3447fdb31836536cc903f1310   
2  dedup::003ab6b40af9b488decea7c582d150a2   
3  dedup::0064f599ed0adb5870a5b3ffe438e485   
4  dedup::00ac8ed3b4327bdd4ebbebcb2ba10a00   

                                        duplicate_id           original_id  \
0  [re3data_____::4af9fe2bb93511a5e0f0c39e94d6557...  [r3d100011306, 2094]   
1  [opendoar____::c6f798b844366ccd65d99bc7f31e0e0...         [3410, 10013]   
2  [https://fairsharing.org/10.25504/FAIRsharing....  [2315, r3d100011894]   
3  [16034, opendoar____::d1f157379ea7e51d4a8c07af...         [16034, 9647]   
4  [610, opendoar____::299fb2142d7de959380f91c01c...           [610, 1426]   

                                                name                  source  \
0  [RESID Database of Protein Modifications, RESI...  [re3data, FAIRsharing]   
1  [erucu: electronic repository of the ukrainian...        [OpenDOAR, roar]   
2                                 [Synapse, Synapse]  [FAIRsharing, re3data]   
3  [Giresun University Institutional Repository, ...        [roar, OpenDOAR]   
4                                 [Hedatuz, hedatuz]        [roar, OpenDOAR]   

                                  unique_id FAIRsharing_id  \
0  [re3data_r3d100011306, FAIRsharing_2094]    [nan, 2094]   
1               [OpenDOAR_3410, roar_10013]     [nan, nan]   
2  [FAIRsharing_2315, re3data_r3d100011894]    [2315, nan]   
3               [roar_16034, OpenDOAR_9647]     [nan, nan]   
4                 [roar_610, OpenDOAR_1426]     [nan, nan]   

             FAIRsharing_type FAIRsharing_attributes.created-at  \
0  [nan, fairsharing-records]   [nan, 2014-11-04T15:23:40.000Z]   
1                  [nan, nan]                        [nan, nan]   
2  [fairsharing-records, nan]   [2016-08-02T13:56:30.000Z, nan]   
3                  [nan, nan]                        [nan, nan]   
4                  [nan, nan]                        [nan, nan]   

  FAIRsharing_attributes.updated-at FAIRsharing_attributes.metadata.doi  \
0   [nan, 2021-09-30T11:38:37.114Z]  [nan, 10.25504/FAIRsharing.qaszjp]   
1                        [nan, nan]                          [nan, nan]   
2   [2021-09-30T11:38:43.134Z, nan]  [10.25504/FAIRsharing.dnxzmk, nan]   
3                        [nan, nan]                          [nan, nan]   
4                        [nan, nan]                          [nan, nan]   

             FAIRsharing_attributes.metadata.name  \
0  [nan, RESID Database of Protein Modifications]   
1                                      [nan, nan]   
2                                  [Synapse, nan]   
3                                      [nan, nan]   
4                                      [nan, nan]   

  FAIRsharing_attributes.metadata.status  \
0                           [nan, ready]   
1                             [nan, nan]   
2                           [ready, nan]   
3                             [nan, nan]   
4                             [nan, nan]   

            FAIRsharing_attributes.metadata.contacts  \
0  [nan, [{'contact-name': 'John S Garavelli', 'c...   
1                                         [nan, nan]   
2  [[{'contact-name': 'Meredith Slota', 'contact-...   
3                                         [nan, nan]   
4                                         [nan, nan]   

  FAIRsharing_attributes.metadata.homepage  \
0  [nan, http://pir.georgetown.edu/resid/]   
1                               [nan, nan]   
2          [https://www.synapse.org/, nan]   
3                               [nan, nan]   
4                               [nan, nan]   

  FAIRsharing_attributes.metadata.identifier  \
0                              [nan, 2094.0]   
1                                 [nan, nan]   
2                              [2315.0, nan]   
3                                 [nan, nan]   
4                                 [nan, nan]   

         FAIRsharing_attributes.metadata.description  \
0  [nan, The RESID Database of Protei

In [30]:
def remove_nan(list_obj):
    if isinstance(list_obj, list):
        while np.nan in list_obj:
            list_obj.remove(np.nan)
    return list_obj
    
dup_within.applymap(remove_nan).to_csv('../data/processed/dup_within.csv')
dup_hybrid.applymap(remove_nan).to_csv('../data/processed/dup_hybrid.csv')
dup_across.applymap(remove_nan).to_csv('../data/processed/dup_across.csv')